In [8]:
import pandas as pd
import numpy as np
%matplotlib inline

from sklearn.impute import SimpleImputer
import sys
import os
import warnings

import matplotlib.pyplot as plt
from tqdm.notebook import tqdm
from statsmodels.graphics.tsaplots import plot_acf

import sklearn
import skforecast
from sklearn.preprocessing import StandardScaler, OrdinalEncoder, MinMaxScaler
from sklearn.feature_selection import RFECV
from sklearn.ensemble import  HistGradientBoostingRegressor, RandomForestRegressor
from skforecast.ForecasterAutoregMultiSeries import ForecasterAutoregMultiSeries
from skforecast.ForecasterAutoreg import ForecasterAutoreg
from skforecast.model_selection import backtesting_forecaster
from skforecast.model_selection import bayesian_search_forecaster
from skforecast.model_selection_multiseries import backtesting_forecaster_multiseries
from skforecast.model_selection_multiseries import bayesian_search_forecaster_multiseries
from skforecast.model_selection_multiseries import select_features_multiseries
from skforecast.plot import set_dark_theme
from skforecast.preprocessing import series_long_to_dict
from skforecast.preprocessing import exog_long_to_dict
from datetime import timedelta
from lightgbm import LGBMRegressor
import utils as u
from sklearn.metrics import classification_report

warnings.filterwarnings('once')

color = '\033[1m\033[38;5;208m'
print(f"{color}Version skforecast: {skforecast.__version__}")
print(f"{color}Version scikit-learn: {sklearn.__version__}")
print(f"{color}Version pandas: {pd.__version__}")
print(f"{color}Version numpy: {np.__version__}")

Version skforecast: 0.13.0
Version scikit-learn: 1.5.2
Version pandas: 2.2.3
Version numpy: 1.26.4


## Loading meme data

In [9]:
gaming = pd.read_csv('../data/processed/gaming.csv')
ai = pd.read_csv('../data/processed/ai.csv')
meme = pd.read_csv('../data/processed/meme.csv')
rwa = pd.read_csv('../data/processed/rwa.csv')

gaming.shape, ai.shape, meme.shape, rwa.shape

((125654, 10), (113423, 10), (33039, 10), (52339, 10))

## Preprocessing data

In [10]:
days_to_predict = 7

In [11]:
class category_data:
    def __init__(self, train_data, test_data, series_dict, exog_dict, future_exog_dict, series_scaler, exog_scaler):
        self.train_data = train_data
        self.test_data = test_data
        self.series_dict = series_dict
        self.exog_dict = exog_dict
        self.future_exog_dict = future_exog_dict
        self.series_scaler = series_scaler
        self.exog_scaler = exog_scaler
        self.forecaster = None
        self.predictions = None
        self.og_train = None
        self.og_test = None
        self.og_pred = None
        self.error_df = None
        self.close_df = None

In [12]:
def generate_data_object(data: pd.DataFrame, days: int):
    train_data, test_data, series_dict, exog_dict, future_exog_dict, series_scaler, exog_scaler = u.preprocess(data, days_to_predict=7)
    data_obj = category_data(train_data, test_data, series_dict, exog_dict, future_exog_dict, series_scaler, exog_scaler)
    return data_obj

In [13]:
gaming_obj = generate_data_object(gaming, days_to_predict)
ai_obj = generate_data_object(ai, days_to_predict)
meme_obj = generate_data_object(meme, days_to_predict)
rwa_obj = generate_data_object(rwa, days_to_predict)

In [14]:
gaming_obj.forecaster = u.train_best_forecaster(gaming_obj.series_dict, gaming_obj.exog_dict, gaming_obj.future_exog_dict, gaming_obj.test_data, future_days=days_to_predict)
ai_obj.forecaster = u.train_best_forecaster(ai_obj.series_dict, ai_obj.exog_dict, ai_obj.future_exog_dict, ai_obj.test_data, future_days=days_to_predict)
meme_obj.forecaster = u.train_best_forecaster(meme_obj.series_dict, meme_obj.exog_dict, meme_obj.future_exog_dict, meme_obj.test_data, future_days=days_to_predict)
rwa_obj.forecaster = u.train_best_forecaster(rwa_obj.series_dict, rwa_obj.exog_dict, rwa_obj.future_exog_dict, rwa_obj.test_data, future_days=days_to_predict)

Training model with parameters: {'colsample_bytree': 0.8, 'learning_rate': 0.01, 'max_depth': 5, 'min_child_samples': 10, 'n_estimators': 100, 'num_leaves': 31, 'subsample': 0.8}
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.003587 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 3885
[LightGBM] [Info] Number of data points in the train set: 80319, number of used features: 16
[LightGBM] [Info] Start training from score 0.000875
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No furth

In [15]:
gaming_obj.predictions = u.predict_X_days(days_to_predict=days_to_predict, forecaster=gaming_obj.forecaster, future_exog_dict=gaming_obj.future_exog_dict)
ai_obj.predictions = u.predict_X_days(days_to_predict=days_to_predict, forecaster=ai_obj.forecaster, future_exog_dict=ai_obj.future_exog_dict)
meme_obj.predictions = u.predict_X_days(days_to_predict=days_to_predict, forecaster=meme_obj.forecaster, future_exog_dict=meme_obj.future_exog_dict)
rwa_obj.predictions = u.predict_X_days(days_to_predict=days_to_predict, forecaster=rwa_obj.forecaster, future_exog_dict=rwa_obj.future_exog_dict)

In [16]:
gaming_obj.og_train, gaming_obj.og_test, gaming_obj.og_pred = u.inverse_scaling(train_df=gaming_obj.train_data, test_df=gaming_obj.test_data, pred_df=gaming_obj.predictions, series_scaler=gaming_obj.series_scaler)
ai_obj.og_train, ai_obj.og_test, ai_obj.og_pred = u.inverse_scaling(train_df=ai_obj.train_data, test_df=ai_obj.test_data, pred_df=ai_obj.predictions, series_scaler=ai_obj.series_scaler)
meme_obj.og_train, meme_obj.og_test, meme_obj.og_pred = u.inverse_scaling(train_df=meme_obj.train_data, test_df=meme_obj.test_data, pred_df=meme_obj.predictions, series_scaler=meme_obj.series_scaler)
rwa_obj.og_train, rwa_obj.og_test, rwa_obj.og_pred = u.inverse_scaling(train_df=rwa_obj.train_data, test_df=rwa_obj.test_data, pred_df=rwa_obj.predictions, series_scaler=rwa_obj.series_scaler)

In [17]:
gaming_obj.close_df = u.get_last_close_info(gaming_obj.og_train, gaming_obj.og_test, gaming_obj.og_pred)
ai_obj.close_df = u.get_last_close_info(ai_obj.og_train, ai_obj.og_test, ai_obj.og_pred)
meme_obj.close_df = u.get_last_close_info(meme_obj.og_train, meme_obj.og_test, meme_obj.og_pred)
rwa_obj.close_df = u.get_last_close_info(rwa_obj.og_train, rwa_obj.og_test, rwa_obj.og_pred)

In [22]:
gaming_obj.close_df

Token ID    last_close  last_test_close  \
0   06963e10-2042-41d3-9583-acb4135460dc  3.398640e-03     3.429296e-03   
1   0844705f-10ed-42ca-b483-914b7d59e351  2.836410e-01     3.097892e-01   
2   10e910bd-6f50-4085-bd78-fbbcde408d28  6.786522e-02     7.049241e-02   
3   1ae14641-7365-4be1-9bb9-c86ab07715b3  9.301679e-01     1.032336e+00   
4   2150225f-b2f2-4b59-bc68-001aa8ae4666  3.202424e-02     3.732745e-02   
5   246715d6-065f-475e-8026-3e0a201c7e33  4.626805e-04     5.688365e-04   
6   24e85250-c2a7-4158-8e7d-244818085463  4.032475e-02     4.317771e-02   
7   30d41b9d-f8eb-4821-8a6e-9016bfd35023  1.822311e-03     1.918915e-03   
8   39268841-e3d8-40b3-8c30-6d6d5bb19bf4  1.452945e-01     1.582443e-01   
9   3a048f18-7aab-4abf-87bd-9f70572c5a9e  3.363081e-03     3.330903e-03   
10  3bb77159-e905-41bf-9321-ca414622cc2b  2.970084e-03     2.894923e-03   
11  3f548a16-866f-4e2c-b3e9-5df6d32d9083  8.194317e-02     9.761059e-02   
12  40aa59cc-c529-4ac7-a8b9-9c20fd8acae5  2.046208e+00     2.143307e+00   
13  42da9689-d86b-40b6-a637-ed56c564edc9  1.397403e-02     1.460060e-02   
14  4315622d-ca20-4ac1-96ee-8667d8b81797  1.955885e-08     1.975076e-08   
15  46f2989f-7eb3-49e4-a32f-5064d6f5b1dc  2.141270e-05     2.973828e-05   
16  50d82ac0-c63a-4c7b-9f7b-d6113ae46617  4.054781e-04     3.882558e-04   
17  52b9da0d-1cb2-4de2-bcf2-1b43cbb584c6  4.750055e+00     5.160549e+00   
18  594c4880-8132-45d1-9c86-68a8b0b18514  7.233183e-02     1.056531e-01   
19  5df45553-ca41-4567-afe2-8077d54992cc  8.253393e-03     8.649199e-03   
20  666b535c-530a-4f32-a7aa-21905cb5b9b7  2.454042e-01     2.765750e-01   
21  67045600-171b-4417-b9e3-db2c5a950dc9  2.619189e+01     2.895200e+01   
22  6a25b7d5-8193-403d-b2b3-b72fd98c55fb  8.986796e-02     1.129784e-01   
23  6a998be7-42e5-4047-b55d-99e058bf2248  2.241843e-02     2.217799e-02   
24  6e87c632-4d4b-4c8f-aa8d-edb52a87125c  2.410610e-04     2.787062e-04   
25  6f3d4d83-badc-4d5a-b487-a70cea172cab  8.069485e-01     1.418562e+00   
26  70ffc67f-2d85-4162-8696-023dbc5f3d13  8.453980e-02     9.319191e-02   
27  7234c1e3-87f4-4a15-b023-daf350f17429  3.770649e-02     4.498751e-02   
28  74a71d75-c6fb-4d73-97ad-7f82ff56aeba  4.277127e-03     4.276185e-03   
29  7a532850-9ec9-4780-94ad-d2759dc1c5cf  3.103036e-02     3.622770e-02   
30  81cb66e8-37b1-4f24-a597-04ee4a0456cc  7.307489e-03     7.599297e-03   
31  83d9ca82-15f9-46ca-a80f-74df4f7a055b  2.269261e-02     2.459273e-02   
32  84a7fc09-daeb-470b-be15-575a493a4069  5.777392e-01     5.768899e-01   
33  8b4ba1e4-6a45-4738-9695-cbe7388760cf  3.291833e-02     3.266044e-02   
34  8c28c829-ac6b-45e8-9cc0-47441be493e1  3.805713e-07     4.237638e-07   
35  8de8d193-45b7-4a95-81ff-4a3c1114a102  1.096070e-04     3.341861e-04   
36  979cf48d-4724-4647-9c6b-1f3d6e23bfca  1.978986e-03     2.018321e-03   
37  98482dd5-6663-4a5f-b93a-b3ac05502123  1.067976e-02     1.125524e-02   
38  9e79e939-dc11-445e-91b9-1e0ec35180fd  2.570639e-01     2.762342e-01   
39  a252b851-675b-4244-a655-3a773ec53584  2.018065e-03     2.459562e-03   
40  a3a65b10-ea76-4cfe-a22a-22bb8455aa99  2.569162e-01     2.816074e-01   
41  a8ef4bc2-b81f-408b-99a8-faef416e1234  1.365281e-02     1.260651e-02   
42  a98165fb-f93b-4a46-8ac3-ea61f14ebe59  1.889717e-02     2.142941e-02   
43  abb61f82-3489-4368-bf0b-407a96a42a49  2.260103e-01     2.433531e-01   
44  adb1789e-2062-44eb-a285-9235e949bb55  1.100313e+00     1.311545e+00   
45  b189d76c-98a1-4b07-868c-eb2460b9f3dc  3.907759e+01     3.988258e+01   
46  b3eeb034-1d5b-4e73-9218-c4cf61d4423d  1.869194e-01     2.085078e-01   
47  bce4e0be-b5c2-4f75-aa27-9c2631418558  4.480193e-02     4.904198e-02   
48  c1b6fdae-1b30-462b-b47d-3f14e212e826  1.476478e-05     1.756938e-05   
49  c1d1a22d-6776-4dd4-bb17-69965948c642  2.669889e-03     2.852234e-03   
50  c2278b42-2ae4-4c4e-9aa8-ea7c6123b0a7  1.035188e-03     1.119959e-03   
51  c5062f88-c5a4-4d4b-b313-8e9682150d46  4.066970e-01     4.261081e-01   
52  def04c24-d3a3-4b80-8eb1-98f9a91c80c9  6.580612e-04   

In [18]:
print("Gaming")
print(classification_report(gaming_obj.close_df['real_went_up'], gaming_obj.close_df['pred_went_up']))
print("AI")
print(classification_report(ai_obj.close_df['real_went_up'], ai_obj.close_df['pred_went_up']))
print("Meme")
print(classification_report(meme_obj.close_df['real_went_up'], meme_obj.close_df['pred_went_up']))
print("RWA")
print(classification_report(rwa_obj.close_df['real_went_up'], rwa_obj.close_df['pred_went_up']))

Gaming
              precision    recall  f1-score   support

         0.0       0.00      0.00      0.00         8
         1.0       0.84      0.82      0.83        50

    accuracy                           0.71        58
   macro avg       0.42      0.41      0.41        58
weighted avg       0.72      0.71      0.71        58

AI
              precision    recall  f1-score   support

         0.0       0.14      0.10      0.12        10
         1.0       0.62      0.71      0.67        21

    accuracy                           0.52        31
   macro avg       0.38      0.41      0.39        31
weighted avg       0.47      0.52      0.49        31

Meme
              precision    recall  f1-score   support

         0.0       0.47      1.00      0.64         8
         1.0       1.00      0.10      0.18        10

    accuracy                           0.50        18
   macro avg       0.74      0.55      0.41        18
weighted avg       0.76      0.50      0.39        18

RWA


In [19]:
gaming_obj.error_df = u.compute_errors(train_data=gaming_obj.og_train, predictions_x_days=gaming_obj.og_pred, test_data=gaming_obj.og_test)
ai_obj.error_df = u.compute_errors(train_data=ai_obj.og_train, predictions_x_days=ai_obj.og_pred, test_data=ai_obj.og_test)
meme_obj.error_df = u.compute_errors(train_data=meme_obj.og_train, predictions_x_days=meme_obj.og_pred, test_data=meme_obj.og_test)
rwa_obj.error_df = u.compute_errors(train_data=rwa_obj.og_train, predictions_x_days=rwa_obj.og_pred, test_data=rwa_obj.og_test)

In [20]:
ai_obj.error_df

Token ID       MSE       MAE          MAPE  \
0   050cd820-2c82-4222-892c-e6f2859625c7  0.000050  0.006986   1422.103931   
1   0bb97d30-b5bb-45d6-b105-e49436cace0e  0.000114  0.009475      2.891446   
2   0d1428e8-2b88-4314-9b1e-aa664b34a5fe  0.000069  0.008073    122.931492   
3   172a1e9a-f56c-4386-85e1-093d801e4e93  0.000030  0.005208     13.957665   
4   18b987bb-2597-4288-a28e-08d7dbce2ee2  0.000034  0.005714    323.757510   
5   196199f6-1c8f-4be4-83dd-733866d6d558  0.000056  0.007371  25458.060422   
6   1e389c02-0a09-4b57-9c50-3a74bca12e4f  0.173044  0.366308      6.760458   
7   1f34fd87-5598-40e7-ac78-7efd6bd28bdd  0.000229  0.014774     19.643994   
8   22820bda-48eb-45bd-b189-af3253ab57c0  0.000015  0.003565     18.170606   
9   3ee65bec-c8c8-482d-ba5c-5c594cc86f2f  0.000075  0.008213     65.918921   
10  42876b1c-10af-47c9-a4f9-853fc207f7b0  0.000027  0.005126    231.643704   
11  490aeb9f-fdf1-4bea-a002-2b294cff0454  0.000025  0.004428      3.958826   
12  5416e814-8023-4f66-aadb-a063afca2414  0.059658  0.194755      4.171339   
13  68221f51-660f-4bed-88e4-680165a9be0c  0.001466  0.031687      6.032859   
14  6a44ac10-0d34-4cf2-a947-53d8bdd54f10  0.000017  0.003813     16.848248   
15  6f67ca1a-5a43-449c-847e-5cfac8d98744  0.002612  0.044320      2.912283   
16  8b88329d-a168-4590-a664-110db3c90308  0.000071  0.008164     14.754369   
17  8cce4515-ed44-4d09-9092-7aef3d046e95  0.000022  0.004667     75.108688   
18  8d807555-a3fa-493c-82bb-fea5c93082f0  0.000033  0.005642    255.106756   
19  978aa54d-1bbb-4f73-bac4-ba7507c27a76  0.000343  0.017085     10.146117   
20  9bb73af8-6ad9-4825-b17c-4ccc6a8fbcf8  0.000030  0.005445    181.792852   
21  a8b53d2d-a2fd-4586-ba67-345e182cc919  0.000284  0.014516      7.743657   
22  aaaac613-ebb5-4af0-ab62-1675cf0a8b8a  0.000017  0.003168      7.367394   
23  aeca591d-3294-42de-bb85-c6a484bacd96  0.247101  0.402012      4.715230   
24  b262d7bb-23ec-475c-8104-c5088e787cb4  0.000019  0.004110     62.487405   
25  b2d068ec-fbd5-4884-beb0-7ad884773733  0.000034  0.005771    262.955261   
26  bc49d919-2925-472d-8bef-e189c0059ccc  0.335199  0.471929      3.199726   
27  d0811fcb-3fcc-41e5-b0f6-cd996b40721e  0.001808  0.038456     15.818557   
28  d1f48a57-2c48-4512-abd6-90e8c29e5aba  0.003623  0.045459      3.167542   
29  ddb361c5-0827-4324-a9ba-ee4fdbf475d9  0.001935  0.037183      2.936259   
30  f59f39ff-5230-42bb-acce-7767dc84cd83  0.000067  0.007870    102.560396   

     MAPE (%)  
0    1422.10%  
1       2.89%  
2     122.93%  
3      13.96%  
4     323.76%  
5   25458.06%  
6       6.76%  
7      19.64%  
8      18.17%  
9      65.92%  
10    231.64%  
11      3.96%  
12      4.17%  
13      6.03%  
14     16.85%  
15      2.91%  
16     14.75%  
17     75.11%  
18    255.11%  
19     10.15%  
20    181.79%  
21      7.74%  
22      7.37%  
23      4.72%  
24     62.49%  
25    262.96%  
26      3.20%  
27     15.82%  
28      3.17%  
29      2.94%  
30    102.56%

In [ ]:
u.plot_predictions(train_data=gaming_obj.og_train, predictions_x_days=gaming_obj.og_pred, test_data=gaming_obj.og_test, last_data_points=120)

In [ ]:
u.plot_predictions(train_data=ai_obj.og_train, predictions_x_days=ai_obj.og_pred, test_data=ai_obj.og_test, last_data_points=60)

In [ ]:
u.plot_predictions(train_data=rwa_obj.og_train, predictions_x_days=rwa_obj.og_pred, test_data=rwa_obj.og_test, last_data_points=60)

In [ ]:
u.plot_predictions(train_data=meme_obj.og_train, predictions_x_days=meme_obj.og_pred, test_data=meme_obj.og_test, last_data_points=60)